<a href="https://colab.research.google.com/github/fadodo/unsupervised_sentinel2__imagery_classification/blob/main/S2_imagery_Clustering_with_GEE.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Preprocessing of Sentinel 2 images from GEE
- Definition of the area of study
- Preprocessing to remove cloud from the image

In [64]:
# importing the necessary packages
# Start Google Earth Engine
# Register to https://earthengine.google.com/
import ee
# for visualization of the image
import geemap

In [65]:
# Authentification to Google earth engine
ee.Authenticate()

# Initialization of the project
ee.Initialize(project='ee-fid')

### Visualization canvas

In [68]:
# Initialize the map canvas
map=geemap.Map()
map

Map(center=[0, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=SearchDataGUI(childr…

### Definition of the Area of Interest
 - get from [geojson.io](https://geojson.io/)

In [69]:
# Get automaticaly the Area of interest coordinate by drawin on the map or use the default AOI
if map.user_roi is not None:
    AOI=map.user_roi
else:
    countries = ee.FeatureCollection(geemap.examples.get_ee_path('countries'))
    AOI = countries.filter(ee.Filter.eq('NAME', 'Togo'))

In [70]:
AOI.getInfo()

{'geodesic': False,
 'type': 'Polygon',
 'coordinates': [[[6.607246, 0.227279],
   [6.607246, 0.415417],
   [6.762428, 0.415417],
   [6.762428, 0.227279],
   [6.607246, 0.227279]]]}

In [72]:
## Identify the centroid coordinates of the AOI
AOI_center=AOI.centroid(1).coordinates().reverse().getInfo()

### Getting Sentinel 2 imagecollection

In [73]:
# Get image of Sentinel 2 harmonized collection of Google Earth Engine for the study area
# filtered on year 2024 for images with 30% less of cloud pixels

S2_aoi= ee.ImageCollection("COPERNICUS/S2_SR_HARMONIZED")\
       .filterDate('2024-01-01','2024-12-31')\
       .filterBounds(AOI)\
       .filter('CLOUDY_PIXEL_PERCENTAGE<= 30')

In [74]:
## Checking the Image collection list
S2_aoi.size().getInfo()

33

### Cloud masking using Scene Classification Layer (SCL)

In [75]:
# Cloud masking using Scene Classification Layer (SCL)
def cloud_mask_scl_fun (image):
  scl = image.select('SCL')
  saturated = scl.eq(1)
  cloud_shadow = scl.eq(3)
  cloud_low_prob = scl.eq(7)
  cloud_med_prob = scl.eq(8)
  cloud_high_prob = scl.eq(9)
  cirrus = scl.eq(10) # 10 = cirrus
  mask = saturated.neq(1)\
               and(cloud_shadow.neq(1))\
               and(cloud_low_prob.neq(1))\
               and(cloud_med_prob.neq(1))\
               and(cloud_high_prob.neq(1))\
               and(cirrus.neq(1))
  return image.updateMask(mask)

In [76]:
# Pass the masking function over the image collection list
S2_aoi_scl=S2_aoi.map(cloud_mask_scl_fun)

In [77]:
# Using the masked images, create a cloud free image by estimating the image band median
# In ee, the image has been scaled by 10000, so return to the original values
S2_aoi_sig = S2_aoi_scl.median().divide(10000)

In [78]:
S2_aoi_sig

### Display the map mosaic

In [79]:
map=geemap.Map(center=AOI_center, zoom=11)
url = 'https://mt1.google.com/vt/lyrs=y&x={x}&y={y}&z={z}'
map.add_tile_layer(url, name='Google Satellite', attribution='Google')
map.addLayer(AOI,{}, 'Area Of Interest')
map.addLayer(S2_aoi_sig,{'bands':['B11','B8', 'B2'], 'min': 0, 'max': 0.5}, "S2_aoi_sig")
#map.add_legend(builtin_legend="ESA_WorldCover")
map.addLayerControl()
map

Map(center=[0.32134800591517937, 6.684836999999834], controls=(WidgetControl(options=['position', 'transparent…

## Saving the free cloud mosaic to google Drive and GEE Assets

Export your best cloud free mosaic image to your google drive, specifying scale and region.

In [54]:
# Export the image to an Earth Engine asset.
task = ee.batch.Export.image.toAsset(**{
  'image': S2_aoi_sig,
  'description': 'S2_aoi_sig',
  'assetId': 'projects/ee-fid/assets/S2_aoi_sig',
  'scale': 20,
  'region': AOI.getInfo()['coordinates'],
  'maxPixels':1e10
})
task.start()

Checking the list and status of task

In [55]:
task.status()

{'state': 'READY',
 'description': 'S2_aoi_sig',
 'priority': 100,
 'creation_timestamp_ms': 1744391743091,
 'update_timestamp_ms': 1744391743091,
 'start_timestamp_ms': 0,
 'task_type': 'EXPORT_IMAGE',
 'id': '4YFSG6YADANAJTMQMKDOHIJW',
 'name': 'projects/ee-fid/operations/4YFSG6YADANAJTMQMKDOHIJW'}

# Unsupervised Land Cover Classification

### Loading the median and cloudless mosaic image saved on gee Assets

In [80]:
## Loading the saved image to free memory
S2_aoi=ee.Image("projects/ee-fid/assets/S2_aoi_sig")

In [81]:
# Checking the mosaic geometry
S2_aoi.geometry()

ee.Geometry({
  "functionInvocationValue": {
    "functionName": "Image.geometry",
    "arguments": {
      "feature": {
        "functionInvocationValue": {
          "functionName": "Image.load",
          "arguments": {
            "id": {
              "constantValue": "projects/ee-fid/assets/S2_aoi_sig"
            }
          }
        }
      }
    }
  }
})

In [82]:
## Get the centroid of the image
img_center=S2_aoi.geometry().centroid().coordinates().reverse().getInfo()

### Creating the random training samples

In [83]:
# Create a radom samples
random_training = S2_aoi.sample(
    region=AOI,
    scale=20,
    numPixels = 1000,
    geometries=True
    );

In [84]:
random_training

In [85]:
# Checking the samples points
map.addLayer(S2_aoi, {'bands':['B11','B8','B2'], 'min':0, 'max':0.5}, 'S2_aoi')
map.setCenter(img_center[1],img_center[0] ,zoom=12)
map.addLayer(random_training,{}, 'Training points')
map

Map(bottom=261976.0, center=[0.3229443739603623, 6.691640388203274], controls=(WidgetControl(options=['positio…

### Method 1 : XMeans Clustering
X-Means is K-Means with an efficient estimation of the number of clusters

In [86]:
# Xmeans Clustering

# initializing and fitting
xmeans=ee.Clusterer.wekaXMeans(5,15).train(random_training);
# Prediction
cluster_xmeans=S2_aoi.cluster(xmeans);

In [87]:
# Visualize the clustered image
map.addLayer(cluster_xmeans.randomVisualizer(),{},'Cluster Xmeans')
map

Map(bottom=523647.0, center=[0.3229443739603623, 6.691640388203274], controls=(WidgetControl(options=['positio…

In [90]:
map.save('xmeans_clusterred.html')

In [88]:
# Checking the class through a selfmask
clax=cluster_xmeans.eq(14);
smask=clax.selfMask();
map.addLayer(smask,{'palette':'red'},"Class")
map

Map(bottom=523647.0, center=[0.3229443739603623, 6.691640388203274], controls=(WidgetControl(options=['positio…

In [89]:
### Remap with the new class to merge together same regions
old_class=[0,1,2,3,4,5,6,7,8,9,10,11,12,13,14]
new_class=[3,3,3,3,3,5,3,11,11,11,11,11,12,11,14]

cluster_xmeans2=cluster_xmeans.remap(old_class,new_class)

In [63]:
## Creating the map with legents
legend_dict = {
    'Open Water': '#466b9f',
    'Coastal cliff': '#ab0000',
    'Buildings': '#d99282',
    'Forest': '#1c5f2c',
    'Smooth surface': '#ab6c28'
}
palette = list(legend_dict.values())

map.addLayer(cluster_xmeans2,{'palette':palette},'Cluster Xmeans2')
map.add_legend(title='Land Cover Type',legend_dict=legend_dict , position='bottomright')
map

Map(bottom=1047142.0, center=[0.2976594886828628, 6.704750061035157], controls=(WidgetControl(options=['positi…

### Export the resulting image to a directory

In [ ]:
# Export the clustered image for later visualization
task = ee.batch.Export.image.toAsset(**{
    'image': cluster_xmeans,
    'description': 'clustered_image',
    'assetId': 'projects/ee-fid/assets/S2_clustered',
    'scale': 20,
    'region': AOI.getInfo()['coordinates'],
    'maxPixels': 1e10
})
task.start()
task.status()

In [ ]:
# download the resulting image to a specific ddirectory
geemap.download_ee_image(cluster_xmeans2, filename='unsupervised.tif', region=AOI, scale=90)

### Method 2 : Learning Vector Quantization (LVQ) Clustering
The algorithm learns by adjusting cluster prototypes based on the input data during training epochs.

In [91]:
# LVQ Clustering

# instantiation and fitting
lvq=ee.Clusterer.wekaLVQ(15).train(random_training);

# Prediction
cluster_lvq=S2_aoi.cluster(lvq);

In [92]:
map.addLayer(cluster_lvq.randomVisualizer(),{},'Cluster lvq')
map

Map(bottom=523647.0, center=[0.3229443739603623, 6.691640388203274], controls=(WidgetControl(options=['positio…

In [93]:
# saving the result
map.save('lvq_clustered.html')

In [94]:
# Checking the class through a selfmask
clax=cluster_lvq.eq(7);
smask=clax.selfMask();
map.addLayer(smask,{'palette':'red'},"Class")
map

Map(bottom=523647.0, center=[0.3229443739603623, 6.691640388203274], controls=(WidgetControl(options=['positio…

In [50]:
### Remap with the new class to merge together same regions
old_class=[0,1,2,3,4,5,6,7,8]
new_class=[0,1,1,1,1,5,1,1,5]

cluster_lvq2=cluster_lvq.remap(old_class,new_class)

In [95]:
map.addLayer(cluster_lvq2.randomVisualizer(),{},"reclassification")
map

Map(bottom=523647.0, center=[0.3229443739603623, 6.691640388203274], controls=(WidgetControl(options=['positio…